# Backtest walkthrough

Backtest involves several key components:
- Account: the account object keeps track of the current state of the account, including cash, positions, and orders.
- Simulated exchange: the exchange object is responsible for matching orders and executing trades.
- Strategy: the strategy object is responsible for generating orders based on market data.
- Executor: the executor object is responsible for executing orders on the exchange.

In [2]:
strategy_config = {
    "class": "TopKDropoutStrategy",
    "module_path": "qlib.contrib.strategy",
    "kwargs": {
        "signal": "<PRED>",
        "topk": 50,
        "n_drop": 5,
    },
}

exchange_config = {
    "limit_threshold": 0.095,
    "deal_price": "close",
    "open_cost": 0.0005,
    "close_cost": 0.0015,
    "min_cost": 5,
}

executor_config = {
    "class": "SimulatorExecutor",
    "module_path": "qlib.backtest.executor",
    "kwargs": {
        "time_per_step": "day",
        "generate_portfolio_metrics": True,
    },
}


In [3]:
from qlib.backtest.account import Account
from qlib.backtest.executor import SimulatorExecutor
from qlib.backtest.exchange import Exchange

## Creating infrastructure

The infrastructure contains `Account` and `Exchange` objects.

Qlib requires us to init the library before using, since benchmark computation 

In [6]:
import qlib
qlib.init(provider_uri="/wsz/Data/my_data_dir/main/cn", region="cn")

[23568:MainThread](2023-06-11 01:47:55,874) INFO - qlib.Initialization - [config.py:432] - default_conf: client.
[23568:MainThread](2023-06-11 01:47:56,141) INFO - qlib.Initialization - [__init__.py:80] - qlib successfully initialized based on client settings.
[23568:MainThread](2023-06-11 01:47:56,143) INFO - qlib.Initialization - [__init__.py:82] - data_path={'__DEFAULT_FREQ': PosixPath('/wsz/Data/my_data_dir/main/cn')}
[23568:MainThread](2023-06-11 01:47:56,144) INFO - qlib.Initialization - [__init__.py:88] - Changing visible CPUs: 190 => 190


We may also need some q4l config to setup benchmark data.

In [9]:
import hydra
from hydra import initialize, compose
import q4l

with hydra.initialize(config_path="../../tests/config", job_name="backtest"):
    cfg = hydra.compose(config_name="base")

/tmp/ipykernel_23568/3796034934.py:5: UserWarning: 
The version_base parameter is not specified.
Please specify a compatability version level, or None.
Will assume defaults for version 1.1
  with hydra.initialize(config_path="../../tests/config", job_name="backtest"):
/opt/conda/envs/dev/lib/python3.8/site-packages/hydra/_internal/defaults_list.py:251: UserWarning: In 'base': Defaults list is missing `_self_`. See https://hydra.cc/docs/1.2/upgrades/1.0_to_1.1/default_composition_order for more information
  warnings.warn(msg, UserWarning)


In [16]:
my_backtest_config = {
    "start_time": "2016-01-01",
    "end_time": "2017-01-01",
    "account": 1e8,
    "benchmark": {  # TODO: Do something to make it real
        "ticker": "^N225",
        "field": "{disk:close} / delay({disk:close}, 1) - 1",
        "backend": "myhxdf",
    },
}


In [12]:
from q4l.data.loader import Q4LDataLoader
loader = Q4LDataLoader(cfg.experiment.data.loader)

In [15]:
loader.storage_backends['disk'].root_dir

'/wsz/Data/my_data_dir/main/jp'

In [18]:
benchmark = loader.compute_alpha_expressions(
    expressions=["{disk:close} / delay({disk:close}, 1) - 1"],
    instruments=["^N225"],
    compute_backend=loader.compute_backends["myhxdf"],
    start_time="2015-03-01",
    end_time=my_backtest_config["end_time"],
    group_name="benchmark",
    names=["return"],
)


In [20]:
benchmark['return']['data']

^N225
2015-03-02       NaN
2015-03-03 -0.000623
2015-03-04 -0.005929
2015-03-05  0.002579
2015-03-06  0.011687
...              ...
2016-12-26 -0.001597
2016-12-27  0.000331
2016-12-28 -0.000069
2016-12-29 -0.013225
2016-12-30 -0.001607

[451 rows x 1 columns]

The `Account` object requires benchmark return data (must be pandas.Series) for computing its excess return.

In [23]:
account = Account(
    init_cash=1e6,
    position_dict={},
    pos_type="Position",
    benchmark_config={'benchmark': benchmark['return']['data']['^N225']}    # If not specified in this way, error will occur
)

In [25]:
account.portfolio_metrics.bench

2015-03-02         NaN
2015-03-03   -0.000623
2015-03-04   -0.005929
2015-03-05    0.002579
2015-03-06    0.011687
                ...   
2016-12-26   -0.001597
2016-12-27    0.000331
2016-12-28   -0.000069
2016-12-29   -0.013225
2016-12-30   -0.001607
Name: ^N225, Length: 451, dtype: float32

Creating the simulated `Exchange` object.

In [26]:
exchange = Exchange(**exchange_config)

Creating the `Executor` object

In [27]:
executor = SimulatorExecutor(**executor_config['kwargs'])

[23568:MainThread](2023-06-11 02:05:52,365) WARNING - qlib.data - [data.py:741] - load calendar error: freq=day, future=True; return current calendar!
[23568:MainThread](2023-06-11 02:05:52,369) WARNING - qlib.data - [data.py:744] - You can get future calendar by referring to the following document: https://github.com/microsoft/qlib/blob/main/scripts/data_collector/contrib/README.md
[23568:MainThread](2023-06-11 02:05:52,397) WARNING - qlib.BaseExecutor - [executor.py:121] - `common_infra` is not set for <qlib.backtest.executor.SimulatorExecutor object at 0x7fab5829f820>


In [28]:
from qlib.backtest.utils import CommonInfrastructure
common_infra = CommonInfrastructure(trade_account=account, trade_exchange=exchange)

In [29]:
executor.reset_common_infra(common_infra)

Create the `Strategy` object

In [41]:
from qlib.contrib.strategy import TopkDropoutStrategy
import pandas as pd
fake_pred = pd.read_csv(
    "/wsz/Data/my_data_dir/main/jp/features/day/close.csv",
    index_col=0,
)
fake_pred.index = pd.to_datetime(fake_pred.index)
fake_pred = fake_pred.stack(dropna=False)
fake_pred.index.set_names(["datetime", "instrument"], inplace=True)
fake_pred.sort_index(inplace=True)
strategy_config['kwargs']['signal'] = fake_pred
strategy = TopkDropoutStrategy(**strategy_config['kwargs'])

In [42]:
strategy.reset_common_infra(common_infra)

Now, let's run the backtest step by step.

In [43]:
executor.reset(start_time=my_backtest_config["start_time"], end_time=my_backtest_config["end_time"])

In [44]:
strategy.reset(executor.get_level_infra())

In [45]:
exchange.codes

'all'

In [56]:
decision = strategy.generate_trade_decision()

/opt/conda/envs/dev/lib/python3.8/site-packages/debugpy/_vendored/pydevd/_pydev_bundle/_pydev_imports_tipper.py:205: FutureWarning: pandas.Float64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  obj = getattr(obj_to_complete, d)
/opt/conda/envs/dev/lib/python3.8/site-packages/debugpy/_vendored/pydevd/_pydev_bundle/_pydev_imports_tipper.py:205: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  obj = getattr(obj_to_complete, d)
/opt/conda/envs/dev/lib/python3.8/site-packages/debugpy/_vendored/pydevd/_pydev_bundle/_pydev_imports_tipper.py:205: FutureWarning: pandas.UInt64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  obj = getattr(obj_to_complete, d)


Get score and signal: 139.11974263191223s


In [53]:
decision.order_list

[]

In [58]:
exe_result = executor.collect_data(decision)

In [59]:
exe_result

<generator object BaseExecutor.collect_data at 0x7fab533e0270>